# Set up imports

In [43]:
# setting up our imports
import re, string, unicodedata
import numpy as np
import pandas as pd
from pprint import pprint
import nltk
from nltk.corpus import stopwords
nltk.download('stopwords')
stop_words = stopwords.words('english')

# Gensim
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel
from gensim.models import LdaModel, LdaMulticore
import gensim.downloader as api
from gensim.models import LsiModel
from gensim.models import ldaseqmodel
from gensim.corpora import Dictionary, bleicorpus
from gensim.matutils import hellinger

nltk.download('wordnet')
from nltk.stem.porter import PorterStemmer
from nltk.stem.wordnet import WordNetLemmatizer
#from bs4 import BeautifulSoup
#from nltk import word_tokenize, sent_tokenize

# Plotting tools 
import pyLDAvis
import pyLDAvis.gensim  # don't skip this
import matplotlib.pyplot as plt
# %matplotlib inline

# Enable logging for gensim - optional
#import logging
#logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.ERROR)
#logging.root.setLevel(level=logging.INFO)
#import warnings
#warnings.filterwarnings("ignore",category=DeprecationWarning)

[nltk_data] Error loading stopwords: <urlopen error [Errno 11002]
[nltk_data]     getaddrinfo failed>
[nltk_data] Error loading wordnet: <urlopen error [Errno 11002]
[nltk_data]     getaddrinfo failed>


# load dataset

In [44]:
# Load dataset
df = pd.read_csv('C:/Users/Kornelius/Desktop/Data 2/nips-papers/papers.csv', header = 0, sep = ';', error_bad_lines=False)
# Drop the columns not needed
df = df.drop(columns=['id', 'event_type', 'pdf_name'], axis=1)

In [45]:
# Drop a row by condition
df = df[df.abstract != 'Abstract Missing']

In [46]:
# sort by year
df = df.sort_values(by=['year'])
df

year                                              title  \
6389  1997        A Neural Network Based Head Tracking System   
5909  1997  Learning Generative Models with the Up Propaga...   
4884  2000   Algorithms for Non-negative Matrix Factorization   
5281  2001  Characterizing Neural Gain Control using Spike...   
4471  2007  Learning Horizontal Connections in a Sparse Co...   
4477  2007                 Predictive Matrix-Variate t Models   
4480  2007                        Competition Adds Complexity   
6095  2007  Progressive mixture rules are deviation subopt...   
6085  2007  Adaptive Embedded Subgraph Algorithms using Wa...   
3564  2007  Estimating disparity with confidence from ener...   
3430  2007          Discriminative Batch Mode Active Learning   
6000  2007   Random Sampling of States in Dynamic Programming   
4515  2007        Mining Internet-Scale Software Repositories   
3434  2007                Computing Robust Counter-Strategies   
5958  2007           The Infinite Gamma-Poisson Feature Model   
4607  2007  Linear programming analysis of loopy belief pr...   
6031  2007  Fitted Q-iteration in continuous action-space ...   
6202  2007  Efficient Convex Relaxation for Transductive S...   
4439  2007  An online Hebbian learning rule that performs ...   
4385  2007  On Ranking in Survival Analysis: Bounds on the...   
6255  2007  The Noisy-Logical Distribution and its Applica...   
4363  2007  Support Vector Machine Classification with Ind...   
3565  2007  Modelling motion primitives and their timing i...   
6271  2007  Modeling image patches with a directed hierarc...   
4276  2007  Gaussian Process Models for Link Analysis and ...   
4226  2007                Spatial Latent Dirichlet Allocation   
6405  2007  Regulator Discovery from Gene Expression Time ...   
6479  2007                            Supervised Topic Models   
3578  2007  EEG-Based Brain-Computer Interaction: Improved...   
6549  2007  A General Boosting Method and its Application ...   
...    ...                                                ...   
5371  2017         Independence clustering (without a matrix)   
5370  2017  Interpretable and Globally Optimal Prediction ...   
5383  2017  From Parity to Preference-based Notions of Fai...   
5368  2017  On Tensor Train Rank Minimization : Statistica...   
5358  2017  Gradients of Generative Models for Improved Di...   
5357  2017  Dual-Agent GANs for Photorealistic and Identit...   
5351  2017  Query Complexity of Clustering with Side Infor...   
3484  2017                       Welfare Guarantees from Data   
5337  2017  Subset Selection and Summarization in Sequenti...   
5327  2017  Clustering Billions of Reads for DNA Data Storage   
5360  2017  Expectation Propagation with Stochastic Kineti...   
5521  2017     Model evidence from nonequilibrium simulations   
5401  2017                Collecting Telemetry Data Privately   
5421  2017  Learning Combinatorial Optimization Algorithms...   
5506  2017  k-Support and Ordered Weighted Sparsity for Ov...   
5501  2017     From Bayesian Sparsity to Gated Recurrent Nets   
5498  2017  Minimax Estimation of Bandable Precision Matrices   
5492  2017  Lower bounds on the robustness to adversarial ...   
5488  2017  Union of Intersections (UoI) for Interpretable...   
5484  2017  Uprooting and Rerooting Higher-Order Graphical...   
5411  2017  When Cyclic Coordinate Descent Outperforms Ran...   
5465  2017  InfoGAIL: Interpretable Imitation Learning fro...   
5450  2017  The Expressive Power of Neural Networks: A Vie...   
5446  2017       Improving the Expected Improvement Algorithm   
5444  2017  Clustering Stable Instances of Euclidean k-means.   
5440  2017  Deliberation Networks: Sequence Generation Bey...   
5436  2017  On the Model Shrinkage Effect of Gamma Process...   
5434  2017      Regret Analysis for Continuous Dueling Bandit   
5459  2017  Identification of Gaussian Process State Space...   
5278  2017                    Hierarchica

In [47]:
df.year.value_counts()

2017    679
2016    569
2014    411
2015    403
2013    360
2012    342
2011    290
2010    288
2009    257
2008    222
2007     99
1997      2
2001      1
2000      1
Name: year, dtype: int64

In [48]:
data = df.abstract.values.tolist()

In [49]:
from nltk.corpus import stopwords 
from nltk.stem.wordnet import WordNetLemmatizer
import string
stop = set(stopwords.words('english'))
exclude = set(string.punctuation) 
lemma = WordNetLemmatizer()
def clean(data):
    stop_free = " ".join([i for i in data.lower().split() if i not in stop])
    punc_free = ''.join(ch for ch in stop_free if ch not in exclude)
    normalized = " ".join(lemma.lemmatize(word) for word in punc_free.split())
    return normalized

data = [clean(data).split() for data in data]  

In [50]:
# remove characters and numbers
def sent_to_words(sentences):
    for sentence in sentences:
        yield(gensim.utils.simple_preprocess(str(sentence), deacc=True))  # deacc=True removes punctuations

data_words = list(sent_to_words(data))

In [51]:
data = data_words
# Create Dictionary
id2word = corpora.Dictionary(data)
print((id2word))

Dictionary(16129 unique tokens: ['adaptation', 'adjusts', 'allows', 'also', 'auxiliary']...)


In [52]:
id2word.filter_n_most_frequent(10)
print((id2word))

Dictionary(16119 unique tokens: ['adaptation', 'adjusts', 'allows', 'also', 'auxiliary']...)


In [53]:
# Create Corpus
texts = data
# Term Document Frequency and creating corpus
corpus = [id2word.doc2bow(text) for text in texts]

In [54]:
from gensim.models import ldaseqmodel
import numpy
from gensim.matutils import hellinger

In [55]:
time_slice = [2 , 1, 1, 99, 222, 257, 288, 290, 342, 360, 411, 403, 569, 679]

In [56]:
#ldaseq = ldaseqmodel.LdaSeqModel(corpus=corpus, id2word=id2word, time_slice=time_slice, num_topics=5)

ldaseq = ldaseqmodel.LdaSeqModel(corpus=corpus , id2word=id2word , num_topics=10, time_slice=time_slice)

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

...

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldaseqmodel.py:230: RuntimeWarning: divide by zero encountered in double_scalars
  convergence = np.fabs((bound - old_bound) / old_bound)


In [57]:
    #ldaseq.print_topics(time=0) # at timeslice 1, those are the topics, word probability to the right 

In [58]:
ldaseq.print_topic_times(topic=0) # evolution of 1st topic through all timeslices

[[('inference', 0.0184667220532077),
  ('distribution', 0.013264870808929985),
  ('process', 0.01276887886827997),
  ('variable', 0.011499561214359945),
  ('bayesian', 0.011456198716204876),
  ('latent', 0.010332347470105363),
  ('structure', 0.00999246608794264),
  ('probabilistic', 0.007901585322507612),
  ('prior', 0.007637154168002698),
  ('using', 0.007571132078650369),
  ('gaussian', 0.007420734152969409),
  ('parameter', 0.006315052270556411),
  ('variational', 0.00629666852959446),
  ('present', 0.006265985781130463),
  ('mixture', 0.005902872020083447),
  ('based', 0.005642864264222661),
  ('markov', 0.0053769557022383),
  ('posterior', 0.005184222423236211),
  ('topic', 0.005132310447243062),
  ('graphical', 0.005013647935775867)],
 [('inference', 0.01853870938755912),
  ('distribution', 0.013307984402029462),
  ('process', 0.012765687576444843),
  ('variable', 0.011492076164497059),
  ('bayesian', 0.011490728499590942),
  ('latent', 0.010361803229575133),
  ('structure', 0.0

In [59]:
ldaseq.print_topic_times(topic=1) 

[[('kernel', 0.021338954360339526),
  ('optimization', 0.01341616987291413),
  ('function', 0.01233160136590423),
  ('gradient', 0.010717913356209793),
  ('convex', 0.009190325063360892),
  ('convergence', 0.008732268413351502),
  ('regularization', 0.007645683701333723),
  ('sparse', 0.007217918449701529),
  ('linear', 0.006905004075490461),
  ('solution', 0.006682634104940538),
  ('based', 0.006398379938359063),
  ('proposed', 0.00592294636740977),
  ('regression', 0.005851972211535392),
  ('feature', 0.00564723519745145),
  ('propose', 0.005616760884515488),
  ('analysis', 0.005561098425080721),
  ('using', 0.005324856546743058),
  ('descent', 0.00532310794158998),
  ('new', 0.005196494471036336),
  ('stochastic', 0.0048176043876433745)],
 [('kernel', 0.021451892772378012),
  ('optimization', 0.013469459489469683),
  ('function', 0.012378247052431447),
  ('gradient', 0.010702729345029801),
  ('convex', 0.009219652362366057),
  ('convergence', 0.008635743646853156),
  ('regularizatio

In [60]:
ldaseq.print_topic_times(topic=2) 

[[('policy', 0.016345521225688945),
  ('decision', 0.011524174567175685),
  ('state', 0.010961687516375525),
  ('action', 0.010874232781452723),
  ('reward', 0.0077070392774372725),
  ('control', 0.007678253413962995),
  ('agent', 0.007571897288362043),
  ('reinforcement', 0.007037234499291451),
  ('process', 0.0069779929061949),
  ('game', 0.0068480917480453546),
  ('human', 0.006713894426114963),
  ('task', 0.006603944579434375),
  ('optimal', 0.00654626512577918),
  ('dynamic', 0.006196105505182449),
  ('using', 0.005956627223120024),
  ('function', 0.005560992773726106),
  ('value', 0.005191719378145945),
  ('environment', 0.005110625700427886),
  ('search', 0.00504815298962393),
  ('strategy', 0.00495882442863991)],
 [('policy', 0.01639096780686453),
  ('decision', 0.011552458154068801),
  ('state', 0.010987771017675587),
  ('action', 0.010900391171472778),
  ('reward', 0.007722883108802688),
  ('control', 0.007693683132614309),
  ('agent', 0.007587330192721682),
  ('reinforcement

In [61]:
ldaseq.print_topic_times(topic=3) 

[[('task', 0.019826507595124374),
  ('classification', 0.013826854092630795),
  ('metric', 0.010623326322493378),
  ('space', 0.010354883621720528),
  ('set', 0.008971406057636477),
  ('classifier', 0.008341954177118353),
  ('information', 0.008107527458170657),
  ('vector', 0.00786429740376996),
  ('distance', 0.0069401320284993495),
  ('proposed', 0.006834597170432262),
  ('multiple', 0.006536986677312215),
  ('prediction', 0.0064465604505757525),
  ('propose', 0.006390420686786027),
  ('feature', 0.006380446222268575),
  ('framework', 0.006177579154962676),
  ('similarity', 0.006142578485305402),
  ('experiment', 0.0058777311639328506),
  ('function', 0.005734107535983986),
  ('structure', 0.005315628750579474),
  ('using', 0.0051807690007356685)],
 [('task', 0.01989366006725762),
  ('classification', 0.013865521889102415),
  ('metric', 0.010649568070468242),
  ('space', 0.010379059340391088),
  ('set', 0.008991107658030857),
  ('classifier', 0.008359485493934065),
  ('information',

In [62]:
ldaseq.print_topic_times(topic=4) 

[[('image', 0.028055622185495167),
  ('feature', 0.018588031112296937),
  ('object', 0.01665261285491947),
  ('human', 0.00694248303014762),
  ('task', 0.006729048514873946),
  ('visual', 0.006525263062692895),
  ('representation', 0.006318557987914096),
  ('training', 0.005929670415855957),
  ('recognition', 0.005794918671513036),
  ('using', 0.0056836544630778345),
  ('set', 0.005632653751555723),
  ('two', 0.005223527633029647),
  ('scene', 0.005107859519390813),
  ('performance', 0.005076345588153496),
  ('detection', 0.005055150369562203),
  ('propose', 0.00474301186365621),
  ('motion', 0.004664418824260908),
  ('learn', 0.004249424436617167),
  ('word', 0.004092533925968432),
  ('use', 0.004042203695095195)],
 [('image', 0.02791223900056994),
  ('feature', 0.018710071124742243),
  ('object', 0.016670283013493204),
  ('human', 0.006965790954427559),
  ('task', 0.006751182233431627),
  ('visual', 0.006546257716529781),
  ('representation', 0.006338527695174124),
  ('training', 0.0

In [63]:
ldaseq.print_topic_times(topic=5) 

[[('signal', 0.027680388717335566),
  ('spike', 0.019892519801588317),
  ('response', 0.00970855507270081),
  ('neuron', 0.009597595934558811),
  ('rate', 0.007706111906553597),
  ('system', 0.007697375427164588),
  ('measurement', 0.005850089510262236),
  ('individual', 0.005521973912525698),
  ('adaptation', 0.005152751129921119),
  ('using', 0.005136479816495856),
  ('phase', 0.0051195377718433275),
  ('mechanism', 0.005092731872463821),
  ('patient', 0.005035566163090988),
  ('disease', 0.005022133480795207),
  ('time', 0.004964668495877749),
  ('noise', 0.004932140572036964),
  ('potential', 0.004620412207045973),
  ('error', 0.004355902763987965),
  ('also', 0.0040357921663883274),
  ('source', 0.003970241005790114)],
 [('signal', 0.027558897440890236),
  ('spike', 0.02003286833341185),
  ('response', 0.009752693546020175),
  ('neuron', 0.009641488827160346),
  ('rate', 0.0077366686263476295),
  ('system', 0.007712901803424174),
  ('measurement', 0.005869154888971052),
  ('indivi

In [64]:
ldaseq.print_topic_times(topic=6) 

[[('network', 0.019930186041653617),
  ('neural', 0.01687366205051488),
  ('input', 0.008773750085605984),
  ('stimulus', 0.008745115849830747),
  ('neuron', 0.008647544121240167),
  ('activity', 0.007846114628473363),
  ('brain', 0.00678199488330766),
  ('deep', 0.006095872753395465),
  ('layer', 0.005318993530789884),
  ('information', 0.0051940397230789016),
  ('representation', 0.004944779445048952),
  ('architecture', 0.004776721143406104),
  ('pattern', 0.004642123845246555),
  ('time', 0.004473361532948398),
  ('system', 0.004242095933259853),
  ('using', 0.004227277922914527),
  ('population', 0.003864793459139589),
  ('memory', 0.003832187276863735),
  ('visual', 0.003791231475107593),
  ('dynamic', 0.003779523732498433)],
 [('network', 0.01973435713796504),
  ('neural', 0.01668935550136547),
  ('stimulus', 0.008791043087568024),
  ('neuron', 0.008691593515120123),
  ('input', 0.008674388933954034),
  ('activity', 0.007884511625443466),
  ('brain', 0.006812241301124634),
  ('d

In [65]:
ldaseq.print_topic_times(topic=7) 

[[('bound', 0.02565502577087374),
  ('function', 0.021484044475535473),
  ('online', 0.012993220794544312),
  ('regret', 0.009852543665763488),
  ('time', 0.008819635346623212),
  ('number', 0.0083674040616059),
  ('provide', 0.006611462885016747),
  ('case', 0.006357029102221615),
  ('graph', 0.006238272787401804),
  ('new', 0.006201100834292244),
  ('approximation', 0.006082504992350536),
  ('complexity', 0.006066035080111402),
  ('optimal', 0.006005074979036396),
  ('setting', 0.005953830479780557),
  ('set', 0.00584065686565839),
  ('also', 0.005666941086958562),
  ('lower', 0.005217908573651248),
  ('guarantee', 0.0051143532629067566),
  ('general', 0.004928820595404574),
  ('bandit', 0.0047291258542682185)],
 [('bound', 0.025760884839421246),
  ('function', 0.021565066550562714),
  ('online', 0.013031799511910705),
  ('regret', 0.00987690610174944),
  ('time', 0.008841048247096658),
  ('number', 0.008386529948224366),
  ('provide', 0.006624714999865343),
  ('case', 0.006369674230

In [66]:
ldaseq.print_topic_times(topic=8) 

[[('clustering', 0.019724301849900597),
  ('matrix', 0.01824216897573555),
  ('sparse', 0.01015285256175282),
  ('graph', 0.008273505010860821),
  ('cluster', 0.007463696396999968),
  ('analysis', 0.007187196642903843),
  ('number', 0.006880600315103817),
  ('sample', 0.006205911197242689),
  ('random', 0.005833115832628991),
  ('component', 0.005038714495319477),
  ('using', 0.004978285865212626),
  ('estimation', 0.004967858562926573),
  ('size', 0.004824383008916434),
  ('set', 0.004768003636715558),
  ('pca', 0.004574024321024858),
  ('point', 0.004566648520653625),
  ('rank', 0.004520018731405289),
  ('subspace', 0.004486942663952063),
  ('noise', 0.004346441440453413),
  ('recovery', 0.004237797431961234)],
 [('clustering', 0.019786588147766144),
  ('matrix', 0.01829833519374675),
  ('sparse', 0.010177282948538667),
  ('graph', 0.008291450894390345),
  ('cluster', 0.007479110442150126),
  ('analysis', 0.007197184735521066),
  ('number', 0.006894306828353034),
  ('sample', 0.00621

In [67]:
ldaseq.print_topic_times(topic=9) 

[[('distribution', 0.018126522502813203),
  ('loss', 0.013815159635392975),
  ('function', 0.00916589215245322),
  ('rate', 0.009107149694740677),
  ('probability', 0.008853697187500582),
  ('error', 0.008371463758830825),
  ('class', 0.008299931879078072),
  ('estimator', 0.008144667013284148),
  ('bound', 0.008019740973394982),
  ('sample', 0.0077923473967001595),
  ('test', 0.007647009598487313),
  ('label', 0.007203343924863533),
  ('estimation', 0.006760898800505381),
  ('risk', 0.006187930533531857),
  ('case', 0.006127150300372551),
  ('prediction', 0.006090798496978995),
  ('estimate', 0.0056873720367866054),
  ('hypothesis', 0.005384250959398692),
  ('classification', 0.005330884679326104),
  ('parameter', 0.00523642817152433)],
 [('distribution', 0.018176461729098835),
  ('loss', 0.01384902525176586),
  ('function', 0.009184742081106182),
  ('rate', 0.009126219086526301),
  ('probability', 0.008871376972262014),
  ('error', 0.008387841430462263),
  ('class', 0.008316344408176

In [68]:
# to check Document - Topic proportions, use `doc-topics`
#doc = ldaseq.doc_topics(558) # check the 558th document in the corpuses topic distribution
#print (doc)
# this document is made up of different topics like this

In [69]:
# make a graph by checking the topic proportions and putting them on a graph 
# same with coherence
# do hellingers distance between topics?

In [70]:
ldaseq.print_topic_times(1) # evolution of 2nd topic through all timeslices


[[('kernel', 0.021338954360339526),
  ('optimization', 0.01341616987291413),
  ('function', 0.01233160136590423),
  ('gradient', 0.010717913356209793),
  ('convex', 0.009190325063360892),
  ('convergence', 0.008732268413351502),
  ('regularization', 0.007645683701333723),
  ('sparse', 0.007217918449701529),
  ('linear', 0.006905004075490461),
  ('solution', 0.006682634104940538),
  ('based', 0.006398379938359063),
  ('proposed', 0.00592294636740977),
  ('regression', 0.005851972211535392),
  ('feature', 0.00564723519745145),
  ('propose', 0.005616760884515488),
  ('analysis', 0.005561098425080721),
  ('using', 0.005324856546743058),
  ('descent', 0.00532310794158998),
  ('new', 0.005196494471036336),
  ('stochastic', 0.0048176043876433745)],
 [('kernel', 0.021451892772378012),
  ('optimization', 0.013469459489469683),
  ('function', 0.012378247052431447),
  ('gradient', 0.010702729345029801),
  ('convex', 0.009219652362366057),
  ('convergence', 0.008635743646853156),
  ('regularizatio

In [71]:
from gensim.models.coherencemodel import CoherenceModel

# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=2)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass1", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV1", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=3)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass2", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV2", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=4)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass3", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV3", cm_DTM.get_coherence())




# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=5)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass4", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV4", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=6)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass5", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV5", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=7)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass6", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV6", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=8)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass7", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV7", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=9)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass8", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV8", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=10)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass9", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV9", cm_DTM.get_coherence())




# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=11)
# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass10", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV10", cm_DTM.get_coherence())


# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=12)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass11", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV11", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=13)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass12", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV12", cm_DTM.get_coherence())

U_Mass1 -2.170272501361955
CV1 0.4275355431248621
U_Mass2 -2.1693548513219882
CV2 0.4275355431248621
U_Mass3 -2.1423875293980403
CV3 0.42762367942997354
U_Mass4 -2.138922402848201
CV4 0.42490913111008755
U_Mass5 -2.115706363557908
CV5 0.43076624286268395
U_Mass6 -2.0862582553232336
CV6 0.43321536807085137
U_Mass7 -2.1165024525420764
CV7 0.43297823464480756
U_Mass8 -2.078036801308584
CV8 0.4296813309665154
U_Mass9 -2.1256706798412037
CV9 0.43347544244175784
U_Mass10 -2.329460208854816
CV10 0.4480771086755868
U_Mass11 -2.27373695631161
CV11 0.4419673044994744
U_Mass12 -2.35253518006033
CV12 0.442042145764972


In [72]:
#graph coherence and topic distribution per time slice

In [73]:
#https://datascience.blog.wzb.eu/2017/11/09/topic-modeling-evaluation-in-python-with-tmtoolkit/